In [1]:
%cd ..

/home/seb/Perso/git/sudoku/sudoku_clean_v2


### Roadmap
- on definit le process de prediction 
- on en deduit le process d'entrainement
- definit un systeme de buffer pour enregistrer X,Y,profondeur
- on code le buffer
- on code l'entrainement pour iterer sur le buffer
- 

## Chose envisager
- on garde les meme buffer/dataloader mais, on en a autant que de profondeurs
- c'est au moment de l'entrainement qu'on choisi sur quel dataloader tapé en fonction de leur profondeur.
- lorsque le niveau 0 est vide on tape sur le plus haut niveau non vide -> non on tape sur le plus peuplé ou on s'en fout


In [2]:
import torch
import pytorch_lightning as pl
from torch import nn
import torch.nn.functional as F
import pandas as pd
import seaborn as sn
import matplotlib.pyplot as plt

from sudoku.models import SmallNetBis, SymPreprocess
from sudoku.loader import DataIterBuffer, train_dataset, test_dataset, data_loader, get_datasets
from sudoku.helper import display_as_dataframe, get_grid_number_soluce
from sudoku.train import SudokuLightning, SudokuTrialErrorLightning, TrialEveryPosException

from collections import deque
from typing import Tuple


from torchmetrics import AUROC
from torch.utils.data.dataset import IterableDataset
from torch.utils.data import  DataLoader

from pytorch_lightning.callbacks import ModelCheckpoint
from lightning_lite.utilities.seed import seed_everything

import numpy as np

from tqdm.auto import tqdm
tqdm.pandas()


import math
def sigmoid(x):
    return 1 / (1 + math.exp(-x))


In [3]:
BATCH_SIZE=32

In [4]:
import lightning.__version__ as v
v

'2.1.3'

In [5]:
tensorboard = pl.loggers.TensorBoardLogger(save_dir="")
torch.cuda.is_available()


True

In [6]:
seed_everything(seed=1)

Global seed set to 1


1

In [8]:
# train_dataset, val_dataset = get_datasets(train_size=1280, test_size=1280)
# train_dataloader = DataLoader(train_dataset, batch_size=32)
# val_dataloader = DataLoader(val_dataset, batch_size=32)

In [9]:
# model = SudokuLightning.load_from_checkpoint(checkpoint_path="/home/seb/Perso/git/sudoku/sudoku_clean_v2/checkpoints/epoch=9-step=4961.ckpt")
model = SudokuTrialErrorLightning.load_from_checkpoint(checkpoint_path="model_9_m3_big_validation_th.ckpt")
# model = SudokuLightning.load_from_checkpoint(checkpoint_path="/home/seb/Perso/git/sudoku/sudoku_clean_v2/lightning_logs/version_21/checkpoints/epoch=99-step=105059.ckpt")#"model_8_m3_100epoch.ckpt")
# /home/seb/Perso/git/sudoku/sudoku_clean_v2/lightning_logs/version_21/checkpoints/epoch=99-step=105059.ckpt
model.reset_threshold_on_validation=False
model.margin=0.6

/home/seb/Perso/git/sudoku/sudoku_clean_v2/venv/lib/python3.10/site-packages/torch/nn/_reduction.py:42: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


In [19]:
board_hardest_sudoku = (
    (8, 0, 0, 0, 0, 0, 0, 0, 0),
    (0, 0, 3, 6, 0, 0, 0, 0, 0),
    (0, 7, 0, 0, 9, 0, 2, 0, 0),
    (0, 5, 0, 0, 0, 7, 0, 0, 0),
    (0, 0, 0, 0, 4, 5, 7, 0, 0),
    (0, 0, 0, 1, 0, 0, 0, 3, 0),
    (0, 0, 1, 0, 0, 0, 0, 6, 8),
    (0, 0, 8, 5, 0, 0, 0, 1, 0),
    (0, 9, 0, 0, 0, 0, 4, 0, 0)
)

In [ ]:
def build_tensor_out_of_grid(grid):
    np_grid = np.asarray(grid) 
    big_grid = np.zeros((1,2,9,9,9), dtype=np.float32)
    for i in range(9):
        big_grid[0,1,:,:,i] = (np_grid==i+1)
        big_grid[0,0,:,:,i] = ((np_grid!=i+1) & (np_grid!=0))
    return torch.from_numpy(big_grid).view(1,2,729)
    

In [ ]:

new_X = build_tensor_out_of_grid(board_hardest_sudoku)

while new_X.sum()<729:
    try:
        new_X = model.predict(new_X)
    except TrialEveryPosException:
        print('''## The grid is super evil!
        please share it as A Discussion in the `Community` tab.
        Except if it is this one: https://www.telegraph.co.uk/news/science/science-news/9359579/Worlds-hardest-sudoku-can-you-crack-it.html''')
        is_valid, new_X = model.backtracking_predict(new_X)
        assert is_valid

In [20]:
# get_grid_number_soluce(grid_17)
# it took 8min39s to return 1

In [22]:
def solve_from_grid(grid, display_grids=True):
    test_x = build_tensor_out_of_grid(grid)
    i = 0

    # print(i, test_x.sum())
    if display_grids:
        display(display_as_dataframe(test_x))
    new_X = model.predict(test_x)
    sum_X= new_X.sum()
    # print(i, new_X.sum())
    if display_grids:
        display(display(display_as_dataframe(new_X)))
    while new_X.sum()<729:
        new_X = model.predict(new_X)
        new_sum_X=new_X.sum()
        assert new_sum_X>sum_X
        sum_X=new_sum_X
        # print(i, new_X.sum())
        i+=1
        if display_grids:
            display(display_as_dataframe(new_X))
    assert model.validate_grids(new_X)
    return new_X

In [23]:
finish_tensor = solve_from_grid(grid_evil_0, display_grids=False)
finish_tensor.sum()

tensor(729.)

In [24]:
finish_tensor = solve_from_grid(grid_17, display_grids=False)
finish_tensor.sum()


tensor(729.)

In [25]:
cols = ['id', 'puzzle', 'solution', 'clues', 'difficulty']
new_data = pd.read_csv("sudoku-3m.csv", skiprows=val_set_size*10, nrows=val_set_size*40)
new_data.columns=cols
new_data.sample(10)


id                                             puzzle  \
8754     72755  ...7....4.543...2..9....7.34....5..2.....6.4.3...   
164023  228024  871..35.9..3..9..8....2....3......6........85....   
3835     67836  41...7..5....4..7.9...5.6.365...1..2.............   
64355   128356  .2..7.54.....8.......91......3....5..95.21..81...   
4516     68517  9....1.24.........6284....9..2..67...4.5...1.....   
88588   152589  .9..7..64....6...218..5....4..68...59....4.1.7...   
174375  238376  9......3..2..78...1....6.89...15...6.......9.....   
78435   142436  ..15.7...3.......487.....9...2.13....1..6...9....   
220216  284217  .73..1.......942..1...2...8368..............7....   
91775   155776  6....1......263.4..5....7.146...............59...   

                                                 solution  clues  difficulty  
8754    6137529847543891262986417534691358725812763493...     24         0.0  
164023  8714635292635794189541286373987152647123469855...     26         2.0  
3835    4138672955263498719781526436547913828972354161...     24         1.0  
64355   8296735414715826935369147822638971547954213681...     24         2.5  
4516    9578613244137296856284351795829167433465789127...     24         1.6  
88588   2951738643479681521864523974126897359587342167...     24         0.0  
174375  9874156323269781541542367892931548765716824936...     24         0.0  
78435   9615472833258967148741325964829136577132658496...     23         2.8  
220216  2738619545867942131495236783682751494529163879...     24         0.0  
91775   6485719321972635482538497614653871298329164759...     24         1.7

In [26]:
for puzzle_str in tqdm(new_data['puzzle']):
    grid = str_to_row_col_grid(puzzle_str)
    # display(grid)
    finish_tensor = solve_from_grid(grid, display_grids=False)
    assert (finish_tensor.sum().item()==729)

  0%|          | 0/256000 [00:00<?, ?it/s]

KeyboardInterrupt: 

- last best index: 11247
- 111640 kb interuption


In [27]:
new_data.iloc[538]

id                                                       100539
puzzle        ...8.....3....657..89....2.52......4..7..435.....
solution      6548721393129465787893154265217389648976243514...
clues                                                        23
difficulty                                                  2.3
Name: 538, dtype: object

In [ ]:
grid

In [25]:

grid = str_to_row_col_grid(new_data.iloc[538]['puzzle'])

finish_tensor = solve_from_grid(grid, display_grids=True)
finish_tensor.sum()

None

tensor(729.)

In [35]:
display_as_dataframe(finish_tensor)

In [36]:
model.validate_grids(finish_tensor)
# voir si ajustement marge suffisant! peut etre prevoir ajuster marge à la ~main avec une method?

tensor([False])

In [ ]:
finish_tensor